In [8]:
import geopandas as gpd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns 

In [9]:
# Caminho para o shapefile
shp_path = r"..\..\Data\Processed\PT-FireSprd_v2.1\L2_FireBehavior\PT-FireProg_v2.1_L2_model_Outubro.shp"

# 1. Ler o shapefile
gdf = gpd.read_file(shp_path)

# 4. Listar as variáveis restantes
print("\n=== Variáveis mantidas para análise ===")
print(gdf.columns.tolist())


=== Variáveis mantidas para análise ===
['ros_p', 'duration_p', 'inidoy', 'enddoy', 'elev_av', 'aspect_sin', 'aspect_cos', 'landform', 'land_use', '1_3y_fir_p', '3_8y_fir_p', '8_ny_fir_p', 'fuel_model', 'f_load_av', 'sW_1m_av', 'sW_3m_av', 'sW_7_av', 'sW_28_av', 'sW_100_av', 'sW_289_av', 't_2m_C_av', 'd_2m_C_av', 'rh_2m_av', 'VPD_Pa_av', 'sP_hPa_av', 'gp_m2s2_av', 'dfmc_av', 'HDW_av', 'Haines_av', 'FWI_12h_av', 'DC_12h_av', 'FFMC_12h_a', 'wv10_kh_av', 'wsin10_av', 'wcos10_av', 'wv100_k_av', 'wsin100_av', 'wcos100_av', 'Recirc', 'CircVar', 't_950_av', 't_850_av', 't_700_av', 't_500_av', 't_300_av', 'rh_950_av', 'rh_850_av', 'rh_700_av', 'rh_500_av', 'rh_300_av', 'wv_950_av', 'wv_850_av', 'wv_700_av', 'wv_500_av', 'wv_300_av', 'wsi_950_av', 'wco_950_av', 'wsi_850_av', 'wco_850_av', 'wsi_700_av', 'wco_700_av', 'wsi_500_av', 'wco_500_av', 'wsi_300_av', 'wco_300_av', 'vwv_950_av', 'vwv_850_av', 'vwv_700_av', 'vwv_500_av', 'vwv_300_av', 'gp_950_av', 'gp_850_av', 'gp_700_av', 'gp_500_av', 'g

In [10]:
# 3. Selecionar apenas as variáveis numéricas
num_df = gdf.select_dtypes(include=["number"])

# 4. Calcular a matriz de correlação
corr_matrix = num_df.corr()

print("\n=== Matriz de correlação (numéricas) ===")
print(corr_matrix)


=== Matriz de correlação (numéricas) ===
               ros_p  duration_p    inidoy    enddoy   elev_av  aspect_sin  \
ros_p       1.000000   -0.428797 -0.042386 -0.044908 -0.135559   -0.017204   
duration_p -0.428797    1.000000  0.019719  0.025611  0.155409   -0.068189   
inidoy     -0.042386    0.019719  1.000000  0.999983 -0.008652   -0.072854   
enddoy     -0.044908    0.025611  0.999983  1.000000 -0.007735   -0.073246   
elev_av    -0.135559    0.155409 -0.008652 -0.007735  1.000000    0.110279   
aspect_sin -0.017204   -0.068189 -0.072854 -0.073246  0.110279    1.000000   
aspect_cos -0.021764    0.011563  0.036348  0.036411  0.149881   -0.078885   
landform    0.092641   -0.153122 -0.050544 -0.051442 -0.099165    0.027160   
land_use   -0.088047    0.137566 -0.049204 -0.048447  0.474010    0.108167   
1_3y_fir_p -0.126289    0.216360  0.016215  0.017488  0.092205   -0.002314   
3_8y_fir_p -0.019369    0.117127  0.150928  0.151598  0.127402   -0.100136   
8_ny_fir_p -0.003119  

In [11]:
plt.figure(
    figsize=(
        max(10, len(corr_matrix.columns)),   # largura proporcional ao nº de variáveis
        max(10, 0.95 * len(corr_matrix.columns))    # altura menor para ficar mais "quadrado"
    )
)

ax = sns.heatmap(
    corr_matrix,
    cmap='coolwarm',
    center=0,
    annot=True,                 # ativa os valores nas células
    fmt=".2f",                  # formato (2 casas decimais)
    annot_kws={"size": 10},      # tamanho da fonte dos labels
    linewidths=0.3,
    cbar_kws={"shrink": 0.8}
)


plt.title(
    "Matriz de Correlação das Variáveis Ambientais e de Velocidade de Propagação do Fogo",
    fontsize=136,   # título maior
    pad=140
)

cbar = ax.collections[0].colorbar
cbar.ax.tick_params(
    labelsize=72,    # tamanho da fonte
    length=30,       # comprimento dos ticks (aumenta o espaço visual)
    width=5,        # largura dos ticks
    direction='out'  # ou 'in' para ticks para dentro
)
# Rótulos maiores e mais legíveis
plt.xticks(rotation=90, fontsize=39)
plt.yticks(rotation=0, fontsize=39)

plt.tight_layout()
plt.savefig("..\..\Data\Data_Exploration\correlation_matrix.pdf", format="pdf", dpi=300, bbox_inches="tight")
plt.show()


In [12]:
import numpy as np
import pandas as pd

n = 200
pd.set_option("display.max_rows", n)  


# Criar matriz sem diagonal
corr_mod = corr_matrix.abs().where(~np.eye(len(corr_matrix), dtype=bool))

# Manter só metade superior da matriz (remove duplicados)
corr_upper = corr_mod.where(np.triu(np.ones(corr_mod.shape), k=1).astype(bool))

# Transformar em DataFrame limpo
df_corr = (
    corr_upper
    .stack()
    .sort_values(ascending=False)
    .reset_index()
)

df_corr.columns = ["Var1", "Var2", "Correlation"]

# Pegar somente top 50
top50 = df_corr.head(n)

print(top50)


           Var1        Var2  Correlation
0        inidoy      enddoy     0.999983
1    LCL_hPa_av    LCL_m_av     0.998932
2      sW_3m_av   sW_289_av     0.993850
3      sW_1m_av   sW_100_av     0.993420
4      rh_2m_av     dfmc_av     0.990967
5     sP_hPa_av  gp_m2s2_av     0.986261
6    wcos100_av  wco_950_av     0.976160
7    wsin100_av  wsi_950_av     0.976091
8     wsin10_av  wsin100_av     0.966578
9     wcos10_av  wcos100_av     0.964040
10   HigCC_p_av  TotCC_p_av     0.962260
11     rh_2m_av  LCL_hPa_av     0.953515
12    wcos10_av  wco_950_av     0.950005
13     sW_3m_av   sW_100_av     0.946810
14     rh_2m_av    LCL_m_av     0.946538
15    t_2m_C_av   VPD_Pa_av     0.945874
16    wsin10_av  wsi_950_av     0.945142
17    gp_500_av   gp_300_av     0.943658
18     sW_1m_av    sW_28_av     0.942585
19      dfmc_av  LCL_hPa_av     0.936319
20    wv_500_av    wSv_5_av     0.935718
21    wv_700_av    wSv_7_av     0.932974
22     sW_1m_av    sW_3m_av     0.931757
23       Recirc 